## **1) Set-up project environment and install package**

In [1]:
from google.colab import drive
drive.mount('/content/drive')
!cp -r /content/drive/MyDrive/NLP_LJP ./ 
import os
current_dir=os.getcwd()
print (current_dir)
os.chdir("/content/NLP_LJP/SwissJudgementPrediction-main/SwissJudgementPrediction-main")
print(os.getcwd())

Mounted at /content/drive
/content
/content/NLP_LJP/SwissJudgementPrediction-main/SwissJudgementPrediction-main


In [2]:
!pip install transformers-interpret

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.3 MB 5.3 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 1.4 MB 37.6 MB/s 
     |████████████████████████████████| 247 kB 49.0 MB/s 
     |████████████████████████████████| 792 kB 36.5 MB/s 
     |████████████████████████████████| 4.4 MB 31.5 MB/s 
     |████████████████████████████████| 1.3 MB 30.1 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 1.3 MB 53.8 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 86 kB 5.4 MB/s 
     |████████████████████████████████| 596 kB 55.7 MB/s 
    

In [3]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
from transformers_interpret import SequenceClassificationExplainer
import math
import pandas as pd

## **2) Load Bert Model (multilingual) and load input data**
*in this project, I focus on French language, you may simply change different language dataset (German or Italy)

In [4]:
MODEL_PATH = "/content/drive/MyDrive/NLP_LJP/bert-base-multilingual-cased/bert-base-multilingual-cased"
model = AutoModelForSequenceClassification.from_pretrained(MODEL_PATH)
tokenizer = AutoTokenizer.from_pretrained(MODEL_PATH, max_length = 2048)
cls_explainer = SequenceClassificationExplainer(model, tokenizer)

In [5]:
datasets = pd.read_csv("/content/NLP_LJP/SwissJudgementPrediction-main/SwissJudgementPrediction-main/data/fr/train.csv")
dataset_ori = pd.DataFrame(datasets)
test_df = dataset_ori["text"].dropna()
# print(test_df.head())
print(dataset_ori.head())


    id                                               text      label  year  \
0   36  A.- Par arrêt du 16 octobre 1995, la Chambre a...  dismissal  2000   
1  100  A.- S._ est affilié à la caisse-maladie INTRAS...  dismissal  2000   
2  134  A.- R._, née en 1955, travaille en qualité d'a...  dismissal  2000   
3  172  A.- Par jugement du 16 juillet 1999, le Présid...   approval  2000   
4  192  A.- Par jugement du 16 juillet 1999, le Présid...   approval  2000   

       chamber origin_canton origin_court origin_chamber  num_tokens_spacy  \
0  CH_BGer_002            JU          NaN            NaN               612   
1  CH_BGer_016            GE          NaN            NaN               610   
2  CH_BGer_016            BE        BE_VG            NaN               188   
3  CH_BGer_006           NaN          NaN            NaN               754   
4  CH_BGer_011           NaN          NaN            NaN               754   

   num_tokens_bert     legal_area      origin_region  
0      

## **3) Full-text Sequence Classification - 10 records per run**
*I have to split the toy size data into 3 sets due to it always lapsed when I run it at one shot.

In [ ]:
subset1=dataset_ori[dataset_ori["num_tokens_bert"] <= 274]
subset=subset1[0:10]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(1) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0 -0.06     1
   attr predc
0 -0.06     1
1  1.73     0
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
4  3.72     1
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
4  3.72     1
5  3.03     1
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
4  3.72     1
5  3.03     1
6  1.65     1
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
4  3.72     1
5  3.03     1
6  1.65     1
7  0.20     0
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
4  3.72     1
5  3.03     1
6  1.65     1
7  0.20     0
8 -0.05     0
   attr predc
0 -0.06     1
1  1.73     0
2  3.72     1
3  0.45     1
4  3.72     1
5  3.03     1
6  1.65     1
7  0.20     0
8 -0.05     0
9  0.62     0


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0 -0.06     1  dismissal
1  1.73     0   approval
2  3.72     1  dismissal
3  0.45     1  dismissal
4  3.72     1  dismissal
5  3.03     1  dismissal
6  1.65     1  dismissal
7  0.20     0  dismissal
8 -0.05     0   approval
9  0.62     0  dismissal
8
accuracy =  80.0 %


In [ ]:
subset1=dataset_ori[dataset_ori["num_tokens_bert"] <= 274]
subset=subset1[10:21]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(1) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0  1.16     0
   attr predc
0  1.16     0
1  4.00     1
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
4  4.00     1
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
4  4.00     1
5  0.21     0
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
4  4.00     1
5  0.21     0
6  2.30     1
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
4  4.00     1
5  0.21     0
6  2.30     1
7  0.36     0
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
4  4.00     1
5  0.21     0
6  2.30     1
7  0.36     0
8  1.36     1
   attr predc
0  1.16     0
1  4.00     1
2  1.35     1
3  0.45     0
4  4.00     1
5  0.21     0
6  2.30     1
7  0.36     0
8  1.36     1
9  2.80     1
    attr predc
0   1.16     0
1   4.00     1
2   1.35     1
3   0.45     0
4   4.00     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

    attr predc      label
0   1.16     0  dismissal
1   4.00     1  dismissal
2   1.35     1  dismissal
3   0.45     0  dismissal
4   4.00     1  dismissal
5   0.21     0  dismissal
6   2.30     1  dismissal
7   0.36     0  dismissal
8   1.36     1  dismissal
9   2.80     1  dismissal
10  2.99     0   approval
7
accuracy =  64.0 %


In [ ]:
subset1=dataset_ori[dataset_ori["num_tokens_bert"] <= 274]
subset=subset1[21:31]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(1) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0 -0.15     0
   attr predc
0 -0.15     0
1 -1.18     1
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
4  1.33     0
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
4  1.33     0
5  1.80     0
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
4  1.33     0
5  1.80     0
6  0.20     0
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
4  1.33     0
5  1.80     0
6  0.20     0
7  0.97     1
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
4  1.33     0
5  1.80     0
6  0.20     0
7  0.97     1
8  1.13     1
   attr predc
0 -0.15     0
1 -1.18     1
2  1.63     1
3  1.13     1
4  1.33     0
5  1.80     0
6  0.20     0
7  0.97     1
8  1.13     1
9  2.44     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0 -0.15     0  dismissal
1 -1.18     1  dismissal
2  1.63     1  dismissal
3  1.13     1  dismissal
4  1.33     0   approval
5  1.80     0   approval
6  0.20     0   approval
7  0.97     1  dismissal
8  1.13     1  dismissal
9  2.44     1  dismissal
9
accuracy =  90.0 %


In [7]:
subset1=dataset_ori[dataset_ori["num_tokens_bert"] <= 274]
subset=subset1[0:31]
tokenlist=subset["num_tokens_bert"]
test_df=subset["text"]
print(tokenlist, test_df)


2      229
6      208
9      201
10     221
11     201
13     224
18     214
20     224
23     228
24     207
25     210
30     183
32     190
34     224
35     183
39     227
42     235
44     199
55     203
56     212
60     212
62     202
63     202
65     186
71     210
77     216
79     206
80     185
84     203
85     210
164    219
Name: num_tokens_bert, dtype: int64 2      A.- R._, née en 1955, travaille en qualité d'a...
6      A.- Au mois d'août 1997, T._ a chargé Me X._, ...
9      A.- Par arrêt du 7 janvier 2000, la Cour crimi...
10     A.- Par décision sur opposition du 21 octobre ...
11     A.- Par arrêt du 7 janvier 2000, la Cour crimi...
13     A.- Par jugement du 11 mai 1999, le Tribunal m...
18     A.- L._, né en 1934, s'est marié le 20 août 19...
20     A.- B._, bénéficie d'une rente entière de l'as...
23     A.- F._, née le 23 avril 1965, a travaillé dès...
24     A.- E._, de nationalité congolaise, est titula...
25     A.- A._, mère de quatre enfants majeurs, domic

## **4) Sub-text Sequence Classification - 10 records per run**
*I have to split the toy size data into 3 sets due to it always lapsed when I run it at one shot. Sub-text is a truncated text from full text due to limitation tokens. The sub-text with highest attribution scores is chosen among the subtexts extracted from a full-text.

In [ ]:
subset=dataset_ori[0:10]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

Token indices sequence length is longer than the specified maximum sequence length for this model (828 > 512). Running this sequence through the model will result in indexing errors


   attr predc
0  1.64     0
   attr predc
0  1.64     0
1  2.05     0
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
4  2.10     1
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
4  2.10     1
5  3.58     0
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
4  2.10     1
5  3.58     0
6  1.73     0
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
4  2.10     1
5  3.58     0
6  1.73     0
7  1.44     0
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
4  2.10     1
5  3.58     0
6  1.73     0
7  1.44     0
8  1.55     0
   attr predc
0  1.64     0
1  2.05     0
2 -0.06     1
3  2.10     1
4  2.10     1
5  3.58     0
6  1.73     0
7  1.44     0
8  1.55     0
9  3.72     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0  1.64     0  dismissal
1  2.05     0  dismissal
2 -0.06     1  dismissal
3  2.10     1   approval
4  2.10     1   approval
5  3.58     0   approval
6  1.73     0   approval
7  1.44     0   approval
8  1.55     0  dismissal
9  3.72     1  dismissal
5
accuracy =  50.0 %


In [ ]:
subset=dataset_ori[10:21]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0  0.45     1
   attr predc
0  0.45     1
1  3.72     1
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
4  1.97     1
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
4  1.97     1
5  4.23     1
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
4  1.97     1
5  4.23     1
6  1.30     0
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
4  1.97     1
5  4.23     1
6  1.30     0
7  1.76     1
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
4  1.97     1
5  4.23     1
6  1.30     0
7  1.76     1
8  1.65     1
   attr predc
0  0.45     1
1  3.72     1
2  1.38     0
3  3.03     1
4  1.97     1
5  4.23     1
6  1.30     0
7  1.76     1
8  1.65     1
9  3.43     0
    attr predc
0   0.45     1
1   3.72     1
2   1.38     0
3   3.03     1
4   1.97     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

    attr predc      label
0   0.45     1  dismissal
1   3.72     1  dismissal
2   1.38     0   approval
3   3.03     1  dismissal
4   1.97     1  dismissal
5   4.23     1   approval
6   1.30     0   approval
7   1.76     1  dismissal
8   1.65     1  dismissal
9   3.43     0  dismissal
10  0.20     0  dismissal
8
accuracy =  73.0 %


In [ ]:
subset=dataset_ori[21:31]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0  1.88     1
   attr predc
0  1.88     1
1  5.93     1
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
4  1.16     0
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
4  1.16     0
5  2.01     1
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
4  1.16     0
5  2.01     1
6  4.81     1
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
4  1.16     0
5  2.01     1
6  4.81     1
7  1.67     0
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
4  1.16     0
5  2.01     1
6  4.81     1
7  1.67     0
8  2.50     1
   attr predc
0  1.88     1
1  5.93     1
2 -0.05     0
3  0.62     0
4  1.16     0
5  2.01     1
6  4.81     1
7  1.67     0
8  2.50     1
9  4.00     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0  1.88     1  dismissal
1  5.93     1  dismissal
2 -0.05     0   approval
3  0.62     0  dismissal
4  1.16     0  dismissal
5  2.01     1  dismissal
6  4.81     1  dismissal
7  1.67     0  dismissal
8  2.50     1  dismissal
9  4.00     1  dismissal
7
accuracy =  70.0 %


In [8]:
subset=dataset_ori[0:31]
tokenlist=subset["num_tokens_bert"]
test_df=subset["text"]
print(tokenlist, test_df)


0      706
1      693
2      229
3      862
4      862
5      991
6      208
7      737
8      968
9      201
10     221
11     201
12     710
13     224
14    1104
15     995
16     933
17     340
18     214
19     422
20     224
21     414
22     918
23     228
24     207
25     210
26     680
27     743
28     790
29     750
30     183
Name: num_tokens_bert, dtype: int64 0     A.- Par arrêt du 16 octobre 1995, la Chambre a...
1     A.- S._ est affilié à la caisse-maladie INTRAS...
2     A.- R._, née en 1955, travaille en qualité d'a...
3     A.- Par jugement du 16 juillet 1999, le Présid...
4     A.- Par jugement du 16 juillet 1999, le Présid...
5     A.- S._, née au Viêt-nam, souffre d'amaurose t...
6     A.- Au mois d'août 1997, T._ a chargé Me X._, ...
7     A.- B.H._, ressortissant yougoslave (province ...
8     A.- Y._, né en 1945, a adhéré le 21 novembre 1...
9     A.- Par arrêt du 7 janvier 2000, la Cour crimi...
10    A.- Par décision sur opposition du 21 octobre ...
11    A

## **5) Full-text Sequence Classification - Visualization**


In [ ]:
subset1=dataset_ori[dataset_ori["num_tokens_bert"] <= 274]
subset=subset1[0:31]
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  sentence =  text[:274]
  sentence2 = tokenizer.decode(sentence)
  word_attributions = cls_explainer(sentence2)
  cls_explainer.visualize("distilbert_viz.html")


Token indices sequence length is longer than the specified maximum sequence length for this model (828 > 512). Running this sequence through the model will result in indexing errors


## **6) Sub-text Sequence Classification - Visualization**

In [ ]:
subset=dataset_ori[0:31]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  print(j)
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      cls_explainer.visualize("distilbert_viz.html") 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      cls_explainer.visualize("distilbert_viz.html")
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      cls_explainer.visualize("distilbert_viz.html")

 

0


1


2


3


4


...

26


27


28


29


30


## **----------------------------------------------------------------------------------------------------------**
##**7) PosterContent----------------------------------**

In [ ]:
textGE1="Sachverhalt: A. Mit Urteil 9C_605/2014 vom 17. September 2014 wies das Bundesgericht eine Beschwerde des A._ gegen einen Entscheid des Versicherungsgerichts des Kantons Solothurn vom 18. Juni 2014 ab, soweit es darauf eintrat. B. A._ ersucht um Revision dieses Entscheids. Die Beschwerde in jenem Verfahren sei gutzuheissen und die Sache an das kantonale Gericht zurÃ¼ckzuweisen, damit dieses in korrekter Zusammensetzung neu entscheide. Es sei ein Schriftenwechsel durchzufÃ¼hren und bei Oberrichter C._ eine Stellungnahme einzuholen. "
word_attributions = cls_explainer(textGE1)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
textGE2="Sachverhalt: A. Mit Strafbefehl vom 21. Juli 2011 bÃ¼sste die Staatsanwaltschaft Lenzburg-Aarau X._ wegen Widerhandlung gegen das BetÃ¤ubungsmittelgesetz mit Fr. 200.--. Auf das hiergegen erhobene Revisionsgesuch vom 25. Juni 2014 trat das Obergericht des Kantons Aargau nicht ein. B. X._ beantragt mit Beschwerde in Strafsachen, der Beschluss des Obergerichts sei aufzuheben und dieses anzuweisen, das Revisionsgesuch materiell zu beurteilen. Die Oberstaatsanwaltschaft und das Obergericht des Kantons Aargau verzichten auf eine Vernehmlassung. "
word_attributions = cls_explainer(textGE2)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
textFR1="Vu : l'ordonnance du 28 novembre 2014 de la Cour de droit pÃ©nal du Tribunal fÃ©dÃ©ral (6B_596/2014), qui dÃ©signe Me Julien Gafner, avocat Ã  Lausanne, en qualitÃ© de dÃ©fenseur d'office de X._, l'arrÃªt du 23 dÃ©cembre 2014 de cette mÃªme cour (6B_596/2014), qui a omis, par inadvertance, d'allouer Ã  Me Julien Gafner une indemnitÃ© d'honoraires d'avocat d'office, vu la lettre du 20 fÃ©vrier 2015, par laquelle Me Julien Gafner dÃ©pose sa note de frais et d'honoraires, "
word_attributions = cls_explainer(textFR1)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
textFR2="Faits : A. Par arrÃªt du 30 mars 2016, la Chambre pÃ©nale du Tribunal cantonal fribourgeois a rejetÃ©, dans la mesure oÃ¹ il Ã©tait recevable, le recours formÃ© par X._ contre une ordonnance du 5 fÃ©vrier 2016, par laquelle le MinistÃ¨re public de l'Ã‰tat de Fribourg a classÃ© la procÃ©dure pÃ©nale ouverte pour violation du secret professionnel Ã  l'encontre des Drs A._ et B._ Ã  la suite d'une plainte pÃ©nale Ã©manant de X._. Elle a Ã©galement rejetÃ© la demande d'assistance judiciaire formÃ©e par cette derniÃ¨re. B. X._ interjette un recours en matiÃ¨re pÃ©nale au Tribunal fÃ©dÃ©ral contre cet arrÃªt dont elle demande l'annulation. Dans ce cadre, elle requiert le bÃ©nÃ©fice de l'assistance judiciaire. "
word_attributions = cls_explainer(textFR2)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
textIT1="Fatti: A. Nell'ambito di un procedimento avviato dinanzi al Consiglio di Stato per denegata giustizia che vedeva una cliente dell'avv. A._ opposta al Municipio di X._ la rappresentante del Governo ticinese, l'avv. I._, ha indetto il 15 marzo 2012 un'udienza istruttoria. Ad udienza conclusa la patrocinata dell'avv. A._ ha chiesto di accertare la nullitÃ  di un allegato della controparte e dell'udienza stessa, criticandone lo svolgimento nonchÃ© la condotta dell'avv. I._, la quale avrebbe agito a suo svantaggio e d'intesa con la controparte. "
word_attributions = cls_explainer(textIT1)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
textIT2="Fatti: A. Il 13 dicembre 2013 il Pretore aggiunto di Bellinzona ha respinto l'azione di responsabilitÃ  con la quale A.A._, agendo per sÃ© e quale cessionaria delle pretese della sorella C.A._, chiedeva che la B._ SA fosse condannata a risarcire fr. 178'647.60 in relazione con l'esecuzione di un mandato di consulenza agli investimenti. Il successivo appello dell'attrice Ã¨ stato respinto, per quanto ricevibile, dalla II Camera civile del Tribunale di appello ticinese con sentenza del 6 novembre 2015. B. A.A._ insorge davanti al Tribunale federale con ricorso in materia civile del 10 dicembre 2015, prevalendosi della violazione del diritto federale e dell'accertamento arbitrario dei fatti; "
word_attributions = cls_explainer(textIT2)
cls_explainer.visualize("distilbert_viz.html")

## **----------------------------------------------------------------------------------------------------------**
##**8) Sequence Classification Workings----------------------------------**

In [ ]:
subset=dataset_ori[0:8]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0  2.13     0
   attr predc
0  2.13     0
1  2.77     1
   attr predc
0  2.13     0
1  2.77     1
2  2.35     1
   attr predc
0  2.13     0
1  2.77     1
2  2.35     1
3  3.41     0
   attr predc
0  2.13     0
1  2.77     1
2  2.35     1
3  3.41     0
4  1.10     0
   attr predc
0  2.13     0
1  2.77     1
2  2.35     1
3  3.41     0
4  1.10     0
5  2.22     1
   attr predc
0  2.13     0
1  2.77     1
2  2.35     1
3  3.41     0
4  1.10     0
5  2.22     1
6  2.46     0
   attr predc
0  2.13     0
1  2.77     1
2  2.35     1
3  3.41     0
4  1.10     0
5  2.22     1
6  2.46     0
7  1.20     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0  2.13     0  dismissal
1  2.77     1   approval
2  2.35     1   approval
3  3.41     0  dismissal
4  1.10     0   approval
5  2.22     1  dismissal
6  2.46     0   approval
7  1.20     1  dismissal
4
accuracy =  50.0 %


In [ ]:
subset=dataset_ori[8:15]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0  3.35     1
   attr predc
0  3.35     1
1  1.66     1
   attr predc
0  3.35     1
1  1.66     1
2  4.20     1
   attr predc
0  3.35     1
1  1.66     1
2  4.20     1
3  4.07     1
   attr predc
0  3.35     1
1  1.66     1
2  4.20     1
3  4.07     1
4  2.50     1
   attr predc
0  3.35     1
1  1.66     1
2  4.20     1
3  4.07     1
4  2.50     1
5  1.99     1
   attr predc
0  3.35     1
1  1.66     1
2  4.20     1
3  4.07     1
4  2.50     1
5  1.99     1
6  2.72     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0  3.35     1  dismissal
1  1.66     1  dismissal
2  4.20     1  dismissal
3  4.07     1  dismissal
4  2.50     1  dismissal
5  1.99     1  dismissal
6  2.72     1   approval
6
accuracy =  86.0 %


In [ ]:
subset=dataset_ori[15:22]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

Token indices sequence length is longer than the specified maximum sequence length for this model (603 > 512). Running this sequence through the model will result in indexing errors


   attr predc
0  5.12     1
   attr predc
0  5.12     1
1  1.83     0
   attr predc
0  5.12     1
1  1.83     0
2  4.70     0
   attr predc
0  5.12     1
1  1.83     0
2  4.70     0
3  3.46     1
   attr predc
0  5.12     1
1  1.83     0
2  4.70     0
3  3.46     1
4  0.74     1
   attr predc
0  5.12     1
1  1.83     0
2  4.70     0
3  3.46     1
4  0.74     1
5  2.68     0
   attr predc
0  5.12     1
1  1.83     0
2  4.70     0
3  3.46     1
4  0.74     1
5  2.68     0
6  4.66     1


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0  5.12     1   approval
1  1.83     0  dismissal
2  4.70     0   approval
3  3.46     1  dismissal
4  0.74     1   approval
5  2.68     0  dismissal
6  4.66     1  dismissal
3
accuracy =  43.0 %


In [ ]:
subset=dataset_ori[22:29]
label=subset["label"]
test_df=subset["text"]
df1 = pd.DataFrame({'attr': pd.Series(dtype='int'),
                   'predc': pd.Series(dtype='int')})
for j in range(len(subset)) :
  text = test_df.iloc[j]
  text = tokenizer.encode(text)
  orilabel = label.iloc[j]
  attr =[]
  predc=[]
  for i in range(math.ceil(len(text)/274)) :
    if (i==0):
      sentence =  text[:274]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    elif (i == math.ceil(len(text)/274)-1):
      sentence =  text[-274:]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    else:
      sentence =  text[274*(i):274*(i+1)]
      sentence2 = tokenizer.decode(sentence)
      word_attributions = cls_explainer(sentence2)
      attri = pd.DataFrame(cls_explainer.word_attributions)
      attrsum = round(attri.iloc[:,1].sum(),2)
      predclass = cls_explainer.predicted_class_index
      attr.append(attrsum)  
      predc.append(predclass) 
    d={'attr':attr, 'predc':predc}
  df = pd.DataFrame(d)
  new_row = df[df["attr"] == df["attr"].max()]
  df1=df1.append(new_row,ignore_index=True)
  print(df1)

   attr predc
0  2.48     0
   attr predc
0  2.48     0
1  3.46     0
   attr predc
0  2.48     0
1  3.46     0
2  2.61     0
   attr predc
0  2.48     0
1  3.46     0
2  2.61     0
3  2.68     0
   attr predc
0  2.48     0
1  3.46     0
2  2.61     0
3  2.68     0
4  2.98     0
   attr predc
0  2.48     0
1  3.46     0
2  2.61     0
3  2.68     0
4  2.98     0
5  2.07     1
   attr predc
0  2.48     0
1  3.46     0
2  2.61     0
3  2.68     0
4  2.98     0
5  2.07     1
6  5.72     0


In [ ]:
label1=pd.DataFrame(label)
label2=label1.reset_index()
df2=df1.reset_index()
final = pd.concat([df2, label2],axis=1)
final = final.drop(["index"], axis=1)
print(final)
accu=0
for j in range(len(final)) :
  if ((final.iloc[j,2]=="approval" and final.iloc[j,1]==0) or (final.iloc[j,2]=="dismissal" and final.iloc[j,1]==1)):
    accu = accu+1
  else:
    accu = accu+0
accuracy=accu/len(final.iloc[:,2])
print(accu)
print("accuracy = ", round(accuracy,2)*100, "%")

   attr predc      label
0  2.48     0  dismissal
1  3.46     0   approval
2  2.61     0  dismissal
3  2.68     0  dismissal
4  2.98     0   approval
5  2.07     1  dismissal
6  5.72     0  dismissal
3
accuracy =  43.0 %


In [ ]:
text="les prévenus auraient mis sur pied une machination frauduleuse ( par le recours à une société fiduciaire étrangère et à des comptes globaux, ainsi que l'usage de quittances en blanc et le caviardage de certains justificatifs afin d'occulter leurs auteurs ) dans le but de tromper le fisc allemand. E. - H. _ forme un recours de droit administratif contre cette dernière ordonnance. Il demande préalablement que l'AFC soit invitée à se prononcer sur l'existence d'une escroquerie fiscale, et que l'autorité étrangère soit invitée à indiquer sur quels éléments de preuve reposent ses soupçons. Principalement, il conclut à l'annulation de l'ordonnance de la Chambre d'accusation et au refus de l'entraide judiciaire. La Chambre d'accusation persiste dans les termes de son ordonnance. Le juge d'instruction a renoncé à se déterminer. L'OFP conclut au rejet du recours dans la mesure où il est recevable. Le recourant a réitéré ses conclusions préalables tendant à l'interpellation de l'AFC."
text = tokenizer.tokenize(text)
print(len(text))


270


In [ ]:
text=test_df[1]
text = tokenizer.tokenize(text)
print(len(text))
if len(text) > 286:
    text = text[-286:]
print(len(text))
print(text)

Token indices sequence length is longer than the specified maximum sequence length for this model (1128 > 512). Running this sequence through the model will result in indexing errors


1128
286
['faux', 'documents', ',', 'l', "'", 'es', '##cro', '##quer', '##ie', 'fiscal', '##e', 'pouvait', 'être', 'rete', '##nue', 'car', 'les', 'pré', '##venu', '##s', 'auraient', 'mis', 'sur', 'pied', 'une', 'mach', '##ination', 'fraud', '##ule', '##use', '(', 'par', 'le', 're', '##cours', 'à', 'une', 'société', 'fi', '##duc', '##iai', '##re', 'é', '##trangère', 'et', 'à', 'des', 'comptes', 'g', '##lob', '##aux', ',', 'ainsi', 'que', 'l', "'", 'usage', 'de', 'quit', '##tan', '##ces', 'en', 'blanc', 'et', 'le', 'ca', '##viar', '##dag', '##e', 'de', 'certains', 'just', '##ifica', '##tifs', 'afin', 'd', "'", 'o', '##cc', '##ulte', '##r', 'leurs', 'auteurs', ')', 'dans', 'le', 'but', 'de', 'tro', '##mper', 'le', 'fi', '##sc', 'allemand', '.', 'E', '.', '-', 'H', '.', '_', 'forme', 'un', 're', '##cours', 'de', 'droit', 'administratif', 'contre', 'cette', 'dernière', 'ordo', '##nnan', '##ce', '.', 'Il', 'demande', 'pré', '##ala', '##blement', 'que', 'l', "'", 'AFC', 'soit', 'invité', '##e

In [ ]:
text="A.- Le 23 décembre 1997, le Ministère public près le Tribunal de grande instance de Francfort-sur-le-Main a adressé à la Suisse une demande d\'entraide judiciaire pour les besoins d\'une enquête dirigée contre A._ et d\'autres personnes, connues ou non, pour fraude fiscale et complicité de fraude fiscale. La demande, qui comporte quelque quarante pages, expose en substance ce qui suit. La société C._ (Genève), fondée par A._ en 1987, disposait de comptes globaux auprès de banques allemandes, notamment B._, ce qui lui permettait d\'intervenir pour le compte de ses clients investisseurs sans que l\'identité de ces derniers n\'apparaisse. Les mouvements de fonds avaient lieu en espèces, par virements postaux, ou en utilisant des quittances signées en blanc par A._. Des gains très importants auraient été réalisés - la demande évoque des délits d\'initiés -, et soustraits au fisc allemand, soit en tout cas 20 à 30 millions de marks depuis 1987. Une filiale de C._ aurait par la suite été créée à Gibraltar (ci-après: C._ Gibraltar) pour réaliser le même genre d\'opérations en évitant le paiement des droits de timbre. L\'autorité requérante demande une perquisition dans les bureaux de C._ et au domicile de A._, ainsi que l\'interrogatoire de ce dernier et de L._, employé de C._. La demande a été transmise par l\'Office fédéral de la police (OFP) au Juge d\'instruction du canton de Genève."
x = tokenizer.encode(text, max_length=2048)
cls_explainer = SequenceClassificationExplainer(model, tokenizer)
word_attributions = cls_explainer(text)


In [ ]:
word_attributions = cls_explainer("Sachverhalt: A. Mit Strafbefehl vom 21. Juli 2011 bÃ¼sste die Staatsanwaltschaft Lenzburg-Aarau X._ wegen Widerhandlung gegen das BetÃ¤ubungsmittelgesetz mit Fr. 200.--. ")
print(word_attributions)
cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('Sa', 0.02381494003385079), ('##ch', 0.038468913426348894), ('##ver', 0.01779840555061054), ('##halt', 0.017226192647742625), (':', 0.09278915644013261), ('A', 0.06393870873752422), ('.', 0.0682781860325975), ('Mit', 0.03390160152810255), ('St', 0.07688886732331339), ('##raf', 0.07878917877534194), ('##be', 0.016569863093187493), ('##fe', 0.045606122966252854), ('##hl', 0.025884270580011803), ('vom', 0.07832051693444435), ('21', 0.07638499544280138), ('.', 0.01877903182830658), ('Juli', 0.03759084496252898), ('2011', 0.16901107375836005), ('b', 0.053699533838407566), ('##Ã', -0.009969252774953521), ('##¼', -0.0047869108640564125), ('##ss', -0.04461729455971261), ('##te', 0.025099212375124722), ('die', 0.05092151036438016), ('Staat', 0.03681093554482121), ('##san', 0.01978432548928444), ('##walt', -0.02084002355415492), ('##schaft', 0.05012131466449653), ('Len', 0.027270210456803026), ('##z', 0.02799985027175166), ('##burg', 0.03143068172692548), ('-', -0.0255273926250

In [ ]:
word_attributions = cls_explainer("Auf das hiergegen erhobene Revisionsgesuch vom 25. Juni 2014 trat das Obergericht des Kantons Aargau nicht ein. ")
print(word_attributions)
cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('Auf', 0.2897554449206584), ('das', 0.04746002575220138), ('hier', 0.01691797762061114), ('##ge', 0.15806845338391146), ('##gen', 0.09252345469095027), ('erhoben', 0.34898297309026083), ('##e', 0.2503963093048126), ('Revision', 0.14316417716200688), ('##sg', 0.08613818089286877), ('##esu', 0.0003043650090355923), ('##ch', 0.10930807238865962), ('vom', 0.11451172125298653), ('25', 0.030546689303738214), ('.', 0.07920363005511152), ('Juni', 0.000659740026456362), ('2014', 0.19060448971905644), ('trat', 0.04615748579100436), ('das', 0.0377346149165336), ('Ober', 0.11698865778404868), ('##gericht', 0.41256659571057597), ('des', 0.188364866958416), ('Kantons', 0.12004149825317817), ('Aa', -0.05490414896328566), ('##rgau', 0.09421490439781069), ('nicht', 0.5073501502329557), ('ein', 0.24602556873969997), ('.', 0.17829379016967833), ('[SEP]', 0.0)]


In [ ]:
word_attributions = cls_explainer("B. X._ beantragt mit Beschwerde in Strafsachen, der Beschluss des Obergerichts sei aufzuheben und dieses anzuweisen, das Revisionsgesuch materiell zu beurteilen. ")
print(word_attributions)
cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('B', 0.10438514106452776), ('.', 0.13725409352758028), ('X', 0.11218547945906553), ('.', 0.1491482811647677), ('_', -0.002870875779269488), ('be', 0.09224791847130895), ('##ant', 0.05001829776180243), ('##rag', 0.10183877906004803), ('##t', 0.07449118759083939), ('mit', 0.1729476523782894), ('Be', 0.06657952455150533), ('##sch', 0.0990296952788267), ('##wer', 0.09274939532536823), ('##de', 0.018964491173016722), ('in', 0.10943935067028605), ('St', 0.0454540797020346), ('##raf', 0.04851401051476536), ('##sache', 0.03816457105089367), ('##n', 0.08669926884584565), (',', 0.060580045843817286), ('der', 0.09323054440165039), ('Be', 0.0009411844012275547), ('##schluss', 0.11184635998494118), ('des', 0.11555310102293825), ('Ober', 0.07230184492304825), ('##gericht', 0.3799718027817157), ('##s', 0.08806633394383087), ('sei', 0.026547314894737554), ('auf', 0.1737577534009509), ('##zu', 0.07306759218938585), ('##heben', 0.02625166878619659), ('und', 0.15379605358945492), ('dies

In [ ]:
word_attributions = cls_explainer("Die Oberstaatsanwaltschaft und das Obergericht des Kantons Aargau verzichten auf eine Vernehmlassung. ")
print(word_attributions)
cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('Die', 0.058669695786774584), ('Oberst', 0.09237910538221712), ('##aat', 0.12204231136230179), ('##san', 0.21101299700199244), ('##walt', 0.3493487106530964), ('##schaft', 0.18306199769713594), ('und', -0.060416199398071926), ('das', 0.10767376862599909), ('Ober', 0.0023783345129487162), ('##gericht', -0.2606526288022443), ('des', -0.1968370241271544), ('Kantons', -0.003742369366635106), ('Aa', 0.14298446212727114), ('##rgau', 0.13685949456735816), ('verzi', 0.3399490230353918), ('##chten', 0.5774011436534131), ('auf', 0.19360079183232176), ('eine', -0.13233468673335824), ('Verne', 0.2189487000054037), ('##hm', 0.0570198894431972), ('##lassung', -0.12412708977438211), ('.', -0.20340930666932514), ('[SEP]', 0.0)]


In [ ]:
word_attributions = cls_explainer("Sachverhalt: A. Mit Strafbefehl vom 21. Juli 2011 bÃ¼sste die Staatsanwaltschaft Lenzburg-Aarau X._ wegen Widerhandlung gegen das BetÃ¤ubungsmittelgesetz mit Fr. 200.--. Auf das hiergegen erhobene Revisionsgesuch vom 25. Juni 2014 trat das Obergericht des Kantons Aargau nicht ein. B. X._ beantragt mit Beschwerde in Strafsachen, der Beschluss des Obergerichts sei aufzuheben und dieses anzuweisen, das Revisionsgesuch materiell zu beurteilen. Die Oberstaatsanwaltschaft und das Obergericht des Kantons Aargau verzichten auf eine Vernehmlassung. ")
print(word_attributions)
cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('Sa', -0.01411828437460039), ('##ch', 0.002195717097495535), ('##ver', -0.011954814751895014), ('##halt', 0.018826184910882234), (':', -0.00945589093237488), ('A', -0.006360201475300474), ('.', 0.016123142979453543), ('Mit', 0.019035992747302288), ('St', -0.027452251678902962), ('##raf', -0.07128185309713149), ('##be', -0.01769177484223931), ('##fe', -0.027365342462037107), ('##hl', -0.0067377291617262735), ('vom', 0.023140655353517774), ('21', 0.011776909272810417), ('.', 0.008422545461491675), ('Juli', -0.003739999049711547), ('2011', -0.027422281628094472), ('b', 0.011662580208190844), ('##Ã', 0.004202174188795563), ('##¼', 0.018661579766482354), ('##ss', -0.0013716975444610104), ('##te', -0.005240971876029911), ('die', 0.00998437556069262), ('Staat', 0.02878358146462914), ('##san', 0.005320086790910957), ('##walt', 0.007200643771339465), ('##schaft', 0.0068943452410827315), ('Len', -0.03153641071266699), ('##z', 0.004715475289106656), ('##burg', 0.0323438610243271

In [ ]:
test_df[1]

'A.- Le 23 décembre 1997, le Ministère public près le Tribunal de grande instance de Francfort-sur-le-Main a adressé à la Suisse une demande d\'entraide judiciaire pour les besoins d\'une enquête dirigée contre A._ et d\'autres personnes, connues ou non, pour fraude fiscale et complicité de fraude fiscale. La demande, qui comporte quelque quarante pages, expose en substance ce qui suit. La société C._ (Genève), fondée par A._ en 1987, disposait de comptes globaux auprès de banques allemandes, notamment B._, ce qui lui permettait d\'intervenir pour le compte de ses clients investisseurs sans que l\'identité de ces derniers n\'apparaisse. Les mouvements de fonds avaient lieu en espèces, par virements postaux, ou en utilisant des quittances signées en blanc par A._. Des gains très importants auraient été réalisés - la demande évoque des délits d\'initiés -, et soustraits au fisc allemand, soit en tout cas 20 à 30 millions de marks depuis 1987. Une filiale de C._ aurait par la suite été cr

In [ ]:
word_attributions = cls_explainer("La demande, qui comporte quelque quarante pages, expose en substance ce qui suit. La société C._ (Genève), fondée par A._ en 1987, disposait de comptes globaux auprès de banques allemandes, notamment B._, ce qui lui permettait d\'intervenir pour le compte de ses clients investisseurs sans que l\'identité de ces derniers n\'apparaisse.")
print(word_attributions)
# cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('La', -0.016066072827791423), ('demande', -0.003950581523055929), (',', 0.021048909666807336), ('qui', -0.04344339099726988), ('comporte', -0.03591218712530623), ('quelque', -0.0018133122292734408), ('quarante', -0.017876314932899828), ('pages', 0.0008207576805976211), (',', -0.001001992445211604), ('expose', -0.04332122454055615), ('en', -0.05226609770653159), ('substance', -0.04047512179744597), ('ce', 0.028123849449322367), ('qui', 0.00967717541470822), ('suit', -0.0006084031224957591), ('.', 0.21017614462364706), ('La', -0.1456563324129983), ('société', -0.272818334903524), ('C', -0.002840344575563908), ('.', 0.01786813486555405), ('_', -0.024469165888870884), ('(', -0.048737071288748074), ('Genève', -0.04611864182207347), (')', 0.004524484483845697), (',', -0.01210109624762199), ('fondée', -0.03369016920043781), ('par', 0.022921247824050424), ('A', -0.016906353041815123), ('.', 0.10052047355600963), ('_', -0.09484662446117158), ('en', -0.0570161195661042), ('1987

In [ ]:
word_attributions = cls_explainer("A.- Le 23 décembre 1997, le Ministère public près le Tribunal de grande instance de Francfort-sur-le-Main a adressé à la Suisse une demande d\'entraide judiciaire pour les besoins d\'une enquête dirigée contre A._ et d\'autres personnes, connues ou non, pour fraude fiscale et complicité de fraude fiscale. La demande, qui comporte quelque quarante pages, expose en substance ce qui suit. La société C._ (Genève), fondée par A._ en 1987, disposait de comptes globaux auprès de banques allemandes, notamment B._, ce qui lui permettait d\'intervenir pour le compte de ses clients investisseurs sans que l\'identité de ces derniers n\'apparaisse.")
print(word_attributions)
cls_explainer.visualize("distilbert_viz.html")

[('[CLS]', 0.0), ('A', -0.07793715580322945), ('.', 0.12704965654410458), ('-', -0.07532237678201274), ('Le', -0.06318811382010746), ('23', -0.004310591448008856), ('décembre', -0.006922789912847152), ('1997', -0.11228528165976025), (',', -0.030972643998422495), ('le', -0.030795545433131795), ('Ministère', -0.008607062001028225), ('public', -0.0023201817178627386), ('près', -0.005251460619890248), ('le', -0.0016211415372082887), ('Tribunal', -0.006375882687473604), ('de', 0.009739610998097288), ('grande', 0.011398731264314066), ('instance', -0.0035538782246617518), ('de', -0.000862305299041222), ('Franc', -0.007156804265681047), ('##fort', 0.007072433272281694), ('-', 0.017284574751501663), ('sur', 0.011237133168021298), ('-', 0.0024129697358020344), ('le', 0.017678233971773316), ('-', 0.010833696052200529), ('Main', -0.014895059358286144), ('a', -0.015154164464607019), ('adres', -0.007421699068195602), ('##sé', -0.008806976239409308), ('à', -0.009410095510299907), ('la', 0.00407414378

In [ ]:
label=dataset_ori["label"]
print(label[1])
text = test_df[1]
text = tokenizer.encode(text)
print(len(text))
print(math.ceil(len(text)/274))
for i in range(math.ceil(len(text)/274)) :
  if (i==0):
    sentence =  text[:274]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    cls_explainer.visualize("distilbert_viz.html")
  elif (i == math.ceil(len(text)/274)-1):
    sentence =  text[-274:]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    cls_explainer.visualize("distilbert_viz.html")
  else:
     sentence =  text[274*(i):274*(i+1)]
     sentence2 = tokenizer.decode(sentence)
     word_attributions = cls_explainer(sentence2)
     print(i)
     cls_explainer.visualize("distilbert_viz.html")


# word_attributions = cls_explainer(text)
# cls_explainer.visualize("distilbert_viz.html")
# print(word_attributions)

approval
1130
5
0


1


2


3


4


In [ ]:
label=dataset_ori["label"]
print(label[2])
text = test_df[2]
text = tokenizer.encode(text)
print(len(text))
print(math.ceil(len(text)/274))
for i in range(math.ceil(len(text)/274)) :
  if (i==0):
    sentence =  text[:274]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    cls_explainer.visualize("distilbert_viz.html")
  elif (i == math.ceil(len(text)/274)-1):
    sentence =  text[-274:]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    cls_explainer.visualize("distilbert_viz.html")
  else:
     sentence =  text[274*(i):274*(i+1)]
     sentence2 = tokenizer.decode(sentence)
     word_attributions = cls_explainer(sentence2)
     print(i)
     cls_explainer.visualize("distilbert_viz.html")

approval
1125
5
0


1


2


3


4


In [ ]:
label=dataset_ori["label"]
print(label[0])
text = test_df[0]
text = tokenizer.encode(text)
print(len(text))
print(math.ceil(len(text)/274))
for i in range(math.ceil(len(text)/274)) :
  if (i==0):
    sentence =  text[:274]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    cls_explainer.visualize("distilbert_viz.html")
  elif (i == math.ceil(len(text)/274)-1):
    sentence =  text[-274:]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    cls_explainer.visualize("distilbert_viz.html")
  else:
     sentence =  text[274*(i):274*(i+1)]
     sentence2 = tokenizer.decode(sentence)
     word_attributions = cls_explainer(sentence2)
     print(i)
     cls_explainer.visualize("distilbert_viz.html")

dismissal
1592
6
0


1


2


3


4


5


In [ ]:
label=dataset_ori["label"]
print(label[31])
print(test_df[31])
text = test_df[31]
text = tokenizer.encode(text)
print(len(text))
print(math.ceil(len(text)/274))
for i in range(math.ceil(len(text)/274)) :
  if (i==0):
    sentence =  text[:274]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    attri = pd.DataFrame(cls_explainer.word_attributions)
    print(cls_explainer.predicted_class_name)
    print(round(attri.iloc[:,1].sum(),2))
  elif (i == math.ceil(len(text)/274)-1):
    sentence =  text[-274:]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    attri = pd.DataFrame(cls_explainer.word_attributions)
    print(cls_explainer.predicted_class_name)
    print(round(attri.iloc[:,1].sum(),2))
  else:
    sentence =  text[274*(i):274*(i+1)]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    attri = pd.DataFrame(cls_explainer.word_attributions)
    print(cls_explainer.predicted_class_name)
    print(round(attri.iloc[:,1].sum(),2))

dismissal
A.- Par arrêt du 16 octobre 1995, la Chambre administrative du Tribunal cantonal du canton du Jura (ci-après: le Tribunal cantonal) a prononcé un avertissement à l'encontre de E._, ressortissant français né en 1963 et titulaire d'une autorisation d'établissement, en ce sens qu'une décision d'expulsion (art. 10 al. 1 lettre d de la loi fédérale du 26 mars 1931 sur le séjour et l'établissement des étrangers [LSEE; RS 142. 20]) ou de rapatriement (art. 11 al. 3 LSEE) serait prononcée s'il devait à nouveau tomber à la charge de l'assistance publique dans un délai déterminé. Constatant que la situation financière de l'intéressé s'était péjorée à l'échéance du délai d'épreuve imparti, la Section jurassienne de l'état civil et des habitants (ci-après: la Section cantonale) a rendu une décision d'expulsion le 21 mars 1997, confirmée le 24 avril suivant. E._ a déféré cette décision devant le Tribunal cantonal. Selon le dispositif du jugement rendu sur ce recours le 25 novembre 1997, l

In [ ]:
label=dataset_ori["label"]
print(label[101])
print(test_df[101])
text = test_df[101]
text = tokenizer.encode(text)
print(len(text))
print(math.ceil(len(text)/274))
for i in range(math.ceil(len(text)/274)) :
  if (i==0):
    sentence =  text[:274]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    attri = pd.DataFrame(cls_explainer.word_attributions)
    print(cls_explainer.predicted_class_name)
    print(round(attri.iloc[:,1].sum(),2))
  elif (i == math.ceil(len(text)/274)-1):
    sentence =  text[-274:]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    attri = pd.DataFrame(cls_explainer.word_attributions)
    print(cls_explainer.predicted_class_name)
    print(round(attri.iloc[:,1].sum(),2))
  else:
    sentence =  text[274*(i):274*(i+1)]
    sentence2 = tokenizer.decode(sentence)
    word_attributions = cls_explainer(sentence2)
    print(i)
    attri = pd.DataFrame(cls_explainer.word_attributions)
    print(cls_explainer.predicted_class_name)
    print(round(attri.iloc[:,1].sum(),2))

dismissal
A.- Ressortissant de l'ex-Yougoslavie, soit du Kosovo, X._ est né le 2 février 1965. Entre 1988 ou 1989 et 1991, X._ a fait plusieurs brefs séjours en Suisse, où il est revenu en octobre 1991. Il y a travaillé sans autorisation, avant de faire l'objet d'un contrôle de police à Genève, où il s'était installé. Il a déposé une demande d'admission provisoire, qui a été admise le 21 avril 1992 par l'Office fédéral des réfugiés, conformément à l'arrêté du Conseil fédéral du 18 décembre 1991. L'intéressé a dès lors été mis au bénéfice d'un permis F, régulièrement renouvelé. Le 27 août 1998, l'Office cantonal de la population du canton de Genève a informé l'Office fédéral des étrangers qu'il était disposé à délivrer à X._ une autorisation de séjour moyennant exception des mesures de limitation selon l'art. 13 lettre f de l'ordonnance du Conseil fédéral limitant le nombre des étrangers du 6 octobre 1998 (OLE; RS 823. 21). Le 1er décembre 1998, l'Office fédéral des étrangers a rendu un

In [ ]:
test="Fatti: A. Il 22 novembre 2012 A._, nato nel 1970, ha riportato una distorsione al ginocchio destro, mentre stava sollevando una termopompa. L'Istituto nazionale di assicurazione contro gli infortuni (INSAI) con decisione del 12 maggio 2014, confermata su opposizione il 5 settembre 2014, ha interrotto l'erogazione di prestazioni di breve durata dal 31 maggio 2014 e rifiutato il versamento di prestazioni di lunga durata, essendo i problemi di salute riconducibili a malattia ed essendo venuta meno la causalitÃ . B. Il Tribunale delle assicurazioni del Cantone Ticino con giudizio del 28 gennaio 2015 ha respinto il ricorso contro la decisione su opposizione. C. A._ presenta un ricorso in materia di diritto pubblico al Tribunale federale chiedendo la riforma del giudizio cantonale nel senso di riconoscere le prestazioni assicurative anche oltre il 31 maggio 2014 sino al termine delle cure. Non sono state chieste osservazioni al ricorso. "
word_attributions = cls_explainer(test)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
test="Fatti: A. Il 3 aprile 2013 l'avv. A._ Ã¨ stata nominata difensore d'ufficio di un imputato domiciliato all'estero. Dopo l'emanazione dell'atto d'accusa, ma prima dello svolgimento del dibattimento di primo grado, questi ha nominato un difensore di fiducia. Il mandato d'ufficio ha di conseguenza preso fine. Con decisione del 9 dicembre 2013, il Presidente della Corte delle assise correzionali di Lugano ha statuito sulla nota d'onorario sottopostagli dall'avvocata, non riconoscendole l'imposta sul valore aggiunto (IVA). B. L'avvocata ha impugnato tale decisione dinanzi alla Corte dei reclami penali del Tribunale d'appello del Cantone Ticino (CRP). Dopo aver chiesto di esprimersi sul gravame anche all'Amministrazione federale delle contribuzioni (AFC), con sentenza del 14 aprile 2014 la CRP ha respinto il reclamo, confermando che le prestazioni fornite dalla legale non soggiacciono all'IVA."
word_attributions = cls_explainer(test)
cls_explainer.visualize("distilbert_viz.html")

In [ ]:
text = "Opferhilfe, hat sich ergeben: A.- Am 20. MÃ¤rz 1994 fiel A._ in RÃ¼dlingen einem TÃ¶tungsdelikt zum Opfer. Mit Urteil vom 16. August 1994 stellte das Kantonsgericht Schaffhausen fest, dass A._ der Vater des am 3. April 1992 geborenen X._ ist. Da sich der Kindsvater nicht mehr am Leben befand, verzichtete das Gericht auf die Festsetzung von UnterhaltsbeitrÃ¤gen. "
class_index = 1

In [ ]:
cls_explainer.predicted_class_index
cls_explainer.predicted_class_name
cls_explainer.visualize("distilbert_viz.html")

array(0)

In [ ]:
cls_explainer.visualize("distilbert_negative_attr.html")

## **----------------------------------------------------------------------------------------------------------**
##**9) Captum Workings----------------------------------**

In [ ]:
def ig_encodings(text):
  pad_id = tokenizer.pad_token_id
  cls_id = tokenizer.cls_token_id
  sep_id = tokenizer.sep_token_id
  input_ids = tokenizer.encode(text)
  base_ids = [pad_id] * len(input_ids)
  input_ids = [cls_id] + input_ids + [sep_id]
  base_ids = [cls_id] + base_ids + [sep_id]
  return torch.tensor(input_ids).to(torch.int64), torch.tensor(base_ids).to(torch.int64)

In [ ]:
from captum.attr import LayerIntegratedGradients, TokenReferenceBase, visualization, IntegratedGradients, configure_interpretable_embedding_layer, remove_interpretable_embedding_layer


In [ ]:
lig = IntegratedGradients(model)

In [ ]:
input_ids, base_ids = ig_encodings(text)
print(f"{input_ids}")
print(f"{base_ids}")
print(f"{len(input_ids)}")
print(f"{len(base_ids)}")

tensor([   101,    101,  42611,  66940,    117,  11250,  10372,  94968,    131,
           138,    119,    118,  11500,  10197,    119,    100,  10444,  30607,
           138,    119,    168,  10106,    155, 110905, 110899, 102576,  10136,
         10745,    157, 110905,    216,  94065,  82836,  51408,  10123,  10580,
         42611,    119,  12699,  97243,  11036,  10250,    119,  10735,  10444,
         23999,  10242,  99472,  55189,  55260, 109294,  10575,  17251,  34519,
           117,  11064,    138,    119,    168,  10118,  18684,  10139,  10392,
           124,    119,  10780,  10450,  67236,  10115,    161,    119,    168,
         10298,    119,  11818,  10372,  10118,  24871,  10107,  60124,  10726,
         12471,  10392,  16182,  29021,    117, 109475,  68106,  10242,  52132,
         10329,  10128,  46657,  40658,  10166,    100,    119,    102,    102])
tensor([101,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0

In [ ]:
tokenizer.convert_ids_to_tokens(input_ids)

['[CLS]',
 '[CLS]',
 'A',
 '.',
 '-',
 'Le',
 '12',
 'avril',
 '1995',
 ',',
 'A',
 '.',
 '_',
 'a',
 'sub',
 '##i',
 'une',
 'ent',
 '##orse',
 'de',
 'la',
 'che',
 '##ville',
 'droite',
 'lors',
 'd',
 "'",
 'une',
 'chute',
 'dans',
 'les',
 'es',
 '##cali',
 '##ers',
 '.',
 'La',
 'Cai',
 '##sse',
 'nationale',
 'suisse',
 'd',
 "'",
 'ass',
 '##urance',
 'en',
 'cas',
 'd',
 "'",
 'accidents',
 '(',
 'CN',
 '##A',
 ')',
 'a',
 'pris',
 'le',
 'cas',
 'en',
 'charge',
 '.',
 '[SEP]',
 '[SEP]']

In [ ]:
attrs, delta = lig.attribute(input_ids, base_ids, target=class_index, return_convergence_delta=True, n_steps=200)

ValueError: ignored